In [146]:
import pandas as pd
import os
from pathlib import Path
import pickle
from datetime import datetime, time, timedelta    
from datetime import datetime
import re

params_df = pd.read_csv('Parameter_B120.csv', parse_dates=['from_date', 'to_date'], dayfirst=True)

pickle_path = r"C:\PICKLE"

output_folder = "processed_csvs"
os.makedirs(output_folder, exist_ok = True)

In [147]:
def get_round(strike_price, gap):
    value = strike_price % gap
    if value > gap/2:
        return strike_price + abs(gap-value)
    return strike_price - value


def calculate_stoploss(dataframe, stoploss_percentage, entry_price):
    stoploss_price = entry_price * (stoploss_percentage/100 + 1)

    condition = dataframe.high >= stoploss_price
    
    stoploss_hit_index = condition.idxmax() if condition.any() else None
    
    return stoploss_hit_index, stoploss_price
    

In [150]:
def get_straddle_strike(synthethic_future_current, file_dataframe, count, start_time, gap):
    
    synthethic_future_previous = synthethic_future_current - gap
    synthethic_future_next = synthethic_future_current + gap
    
    file_dataframe = file_dataframe[file_dataframe.date_time.dt.strftime('%H:%M:%S') >= f'{start_time}']
    file_dataframe = file_dataframe[file_dataframe.date_time.dt.strftime('%H:%M:%S') <= f'{end_time}']

    df_current = file_dataframe[file_dataframe.scrip.str.contains(f'{synthethic_future_current}')]
    df_previous = file_dataframe[file_dataframe.scrip.str.contains(f'{synthethic_future_previous}')]
    df_next = file_dataframe[file_dataframe.scrip.str.contains(f'{synthethic_future_next}')]

    # Ensure start_time is a time object
    if isinstance(start_time, str):
        start_time = datetime.strptime(start_time, "%H:%M:%S").time()

    # Now it should pass the isinstance check
    if isinstance(start_time, time):
        start_time = datetime.combine(datetime.today(), start_time)
        
        
    start_time_temp = start_time
    min_start_time = start_time
    
    
    previous_diff = 10000000
    current_diff = 10000000 
    next_diff = 10000000
    
    time_flag = False
    count2 = 0
    print("heel")
    while time_flag == False:

        if len(df_current[df_current.date_time.dt.strftime('%H:%M:%S') == start_time.strftime('%H:%M:%S')]) >= 2:
            time_flag = True
            current_diff = min(current_diff, abs(df_current.close.iloc[0] - df_current.close.iloc[1]))
            
            
            
        if len(df_previous[df_previous.date_time.dt.strftime('%H:%M:%S') == start_time.strftime('%H:%M:%S')]) >= 2:
            time_flag = True
            previous_diff = min(previous_diff, abs(df_previous.close.iloc[0] - df_previous.close.iloc[1]))
            
            
        if len(df_next[df_next.date_time.dt.strftime('%H:%M:%S') == start_time.strftime('%H:%M:%S')]) >= 2:
            time_flag = True
            next_diff = min(next_diff, abs(df_next.close.iloc[0] - df_next.close.iloc[1]))
            
        start_time += timedelta(minutes = 1) 
        print(start_time)
        if time_flag == True:
            minimum_diff = min(previous_diff, min(current_diff, next_diff))
            
            if minimum_diff == previous_diff:
                return synthethic_future_previous

            elif minimum_diff == next_diff:
                return synthethic_future_next

            return synthethic_future_current

In [151]:
for _, row in params_df.iterrows():
    index = row['index']
    start_date = row['from_date']
    end_date = row['to_date']
    start_time = row['entry_time']
    end_time = row['exit_time']
    orderside = row['orderside']
    method = row['method']
    sl = row['sl']
    ut_sl =  row['ut_sl']
    om = row['om']
    gap_price = row['gap_price']
    slippage = row['slippage']
    
    if index == 'FINNIFTY' or index == 'SENSEX' or index == 'NIFTY' or index == 'BANKNIFTY' or index == 'MIDCPNIFTY':
        continue
    
    file_index_dict = {
        'SENSEX' : 'SX',
        'NIFTY' : 'Nifty',
        'FINNIFTY' : 'FN',
        'BANKNIFTY' : 'BN',
        'MIDCPNIFTY' : 'MCN',
        'BANKEX' : 'BX'
    }
    
    file_index = file_index_dict[index]
    
    future_folder = os.path.join(pickle_path, f"{file_index} Future")
    option_folder = os.path.join(pickle_path, f"{file_index} Options")
    
    

    pkl_future_files = [file for file in os.listdir(future_folder) if file.endswith('.pkl')]
    pkl_option_files = [file for file in os.listdir(option_folder) if file.endswith('.pkl') and \
                        datetime.strptime(file[:10], "%Y-%m-%d") >= start_date and \
                        datetime.strptime(file[:10], "%Y-%m-%d") <= end_date] 
        
    future_strike_price_dict = {}
    future_strike_price_round_dict = {}
    
    dte_df = pd.read_csv('DTE.csv')
    
    print(index)
        
    for file in pkl_future_files:
        df = pd.read_pickle(f"{future_folder}/{file}")

        if 'scrip' in df.columns:
            df = df[df.scrip.str.endswith(f'{index}-I')]
        else:
            df = df[df['index'].str.endswith(f'{index}')]
            

        start_time = start_time.zfill(8)
        
        df = df[df.date_time.dt.strftime('%H:%M:%S') >= f'{start_time}']
        df = df[df.date_time.dt.strftime('%H:%M:%S') <= f'{end_time}']
        
        future_strike_price = df.close.iloc[0]
        future_date = str(df.date_time.dt.date.iloc[0])
        
        
        future_strike_price_round_dict[future_date] = str(get_round(int(future_strike_price), gap_price))
        future_strike_price_dict[future_date] = str(future_strike_price)

    count = 0
    data_list = []

    for file in pkl_option_files:
        if count < 100:
            count+=1
            continue
        if count == 103:
            count+=1
            continue
            
        dataframe1 = pd.read_pickle(f"{option_folder}/{file}")

        option_date = str(dataframe1.date_time.dt.date.iloc[0])
        strike = int(future_strike_price_round_dict[option_date])

        strike_ce_current = f"{strike}CE"
        strike_pe_current = f"{strike}PE"

        if dataframe1['scrip'].dtype != 'category':
            dataframe1['scrip'] = dataframe1['scrip'].astype('category')   
        matching_categories = [cat for cat in dataframe1.scrip.cat.categories if strike_ce_current in cat or strike_pe_current in cat]
        df1 = dataframe1[dataframe1.scrip.isin(matching_categories)]

        if df1.empty:
            print(f"Skipping {file} as no data is available in the given time range ({start_time} - {end_time})")
            continue  # Skip this file

        this_date = df1.date_time.dt.strftime('%d-%m-%Y').iloc[0]
        this_day = str(df1.date_time.dt.day_name().iloc[0])
        #this_dte = dte_df.loc[, [Date = this_date, index ]]
        this_dte = dte_df.loc[dte_df["Date"] == this_date, f'{index}'].values[0]

        df2 = df1[df1.scrip.str.contains('CE')]
        df3 = df1[df1.scrip.str.contains('PE')]

        time_flag = False
        print("ha")
        while not time_flag:
            
            if (df2.date_time.dt.strftime("%H:%M:%S") == start_time).any() and \
                (df3.date_time.dt.strftime("%H:%M:%S") == start_time).any():
                time_flag = True
                print("start_time found")
                
            elif start_time == '15:25:00':
                print("skipping file as values absent in it")
                breakall = True
                continue
                
            else:
                if isinstance(start_time, str):
                    start_time = datetime.strptime(start_time, "%H:%M:%S").time()
                    
                if isinstance(start_time, time):
                    start_time = datetime.combine(datetime.today(), start_time)
                    
                start_time += timedelta(minutes = 1)
                start_time = start_time.strftime("%H:%M:%S")
                print(start_time)
                
        print("he")
        
                
        df2 = df2[df2.date_time.dt.strftime('%H:%M:%S') >= f'{start_time}']
        df2 = df2[df2.date_time.dt.strftime('%H:%M:%S') <= f'{start_time}']

        df3 = df3[df3.date_time.dt.strftime('%H:%M:%S') >= f'{start_time}']
        df3 = df3[df3.date_time.dt.strftime('%H:%M:%S') <= f'{start_time}']

        current_call_entry_price = df2.close.iloc[0]
        current_put_entry_price = df3.close.iloc[0]

        synthethic_future = strike + current_call_entry_price - current_put_entry_price
        synthethic_future = int(get_round(synthethic_future, gap_price))

        straddle_strike = get_straddle_strike(synthethic_future, dataframe1, count, start_time, gap_price)
        print(straddle_strike)


        dataframe1 = dataframe1[dataframe1.date_time.dt.strftime('%H:%M:%S') >= f'{start_time}']
        dataframe1 = dataframe1[dataframe1.date_time.dt.strftime('%H:%M:%S') <= f'{end_time}']

        dataframe2 = dataframe1[dataframe1.scrip.str.contains(f'{straddle_strike}CE')]
        dataframe3 = dataframe1[dataframe1.scrip.str.contains(f'{straddle_strike}PE')]

        call_entry_price = dataframe2.close.iloc[0]
        put_entry_price = dataframe3.close.iloc[0]

        call_exit_price = dataframe2.close.iloc[-1]
        put_exit_price = dataframe3.close.iloc[-1]

        call_stoploss_index, call_stoploss_price = calculate_stoploss(dataframe2.iloc[1:], sl, call_entry_price)
        put_stoploss_index, put_stoploss_price = calculate_stoploss(dataframe3.iloc[1:], sl, put_entry_price)

        dataframe_filter_2 = dataframe2[dataframe2.date_time.dt.strftime('%H:%M:%S') > f'{start_time}']
        dataframe_filter_3 = dataframe3[dataframe3.date_time.dt.strftime('%H:%M:%S') > f'{start_time}']

        call_high = dataframe_filter_2.high.max()
        put_high = dataframe_filter_3.high.max()
        call_low = dataframe_filter_2.low.min()
        put_low = dataframe_filter_3.low.min()

        call_stoploss_flag = True if call_stoploss_index != None else False
        put_stoploss_flag = True if put_stoploss_index != None else False

        call_stoploss_time = dataframe2.date_time.loc[call_stoploss_index] if call_stoploss_flag else ""
        put_stoploss_time = dataframe3.date_time.loc[put_stoploss_index] if put_stoploss_flag else ""

        call_pnl = call_entry_price - call_stoploss_price if call_stoploss_flag else call_entry_price - call_exit_price
        put_pnl = put_entry_price - put_stoploss_price if put_stoploss_flag else put_entry_price - put_exit_price

        call_pnl = round(call_pnl - slippage*call_entry_price, 2)
        put_pnl = round(put_pnl - slippage * put_entry_price, 2)

        thi_date = pd.to_datetime(this_date, format = '%d-%m-%Y')
        thi_date = thi_date.date().strftime('%Y-%m-%d')

        data_list.append({
            'Date' : pd.to_datetime(this_date, format = '%d-%m-%Y'),
            'Day' : this_day,
            'DTE' : int(this_dte),
            'EntryTime' : start_time,
            'Future' : future_strike_price_dict[thi_date],
            'CE.Strike' : f'{straddle_strike}CE',
            'CE.Open' : call_entry_price,
            'CE.High' : call_high,
            'CE.Low' : call_low,
            'CE.Close' : call_exit_price,
            'CE.SL.Flag' : call_stoploss_flag,
            'CE.SL.Time' : call_stoploss_time,
            'CE.PNL' :  call_pnl,
            'PE.Strike' : f'{straddle_strike}PE',
            'PE.Open' : put_entry_price,
            'PE.High' : put_high,
            'PE.Low' : put_low,
            'PE.Close' : put_exit_price,
            'PE.SL.Flag' : put_stoploss_flag,
            'PE.SL.Time' : put_stoploss_time,
            'PE.PNL' : put_pnl
        })
        

        #UT.Strike	UT.Open	UT.High	UT.Low	UT.Close	UT.SL.Flag	UT.SL.Time	BPL	TT.PL.AT.SL	UT.PL.AT.SL	UT.PNL	Total.PNL
        count+=1

        print(count)
        print()



    df_output = pd.DataFrame(data_list)  # Convert list of dicts to DataFrame

    safe_filename = f"{index} {start_time} {end_time} {sl} {ut_sl} {om}.csv"
    safe_filename = re.sub(r'[<>:"/\\|?*]', '', safe_filename)  # Replace invalid characters


    output_path = os.path.join(output_folder, safe_filename)
    df_output.to_csv(output_path, index=False)  # Save as CSV without index

    print(f"File saved at: {output_path}")  # Debugging message
    df_output


BANKEX
ha
start_time found
he
heel
        index    scrip           date_time    open    high     low   close  \
140    BANKEX  55800CE 2024-05-30 09:20:00  637.45  657.20  625.90  653.85   
141    BANKEX  55800PE 2024-05-30 09:20:00  688.75  688.75  650.00  681.15   
174    BANKEX  55800CE 2024-05-30 09:21:00  674.25  674.25  648.05  660.00   
175    BANKEX  55800PE 2024-05-30 09:21:00  681.10  681.15  681.10  681.15   
206    BANKEX  55800CE 2024-05-30 09:22:00  649.10  654.30  617.15  617.15   
...       ...      ...                 ...     ...     ...     ...     ...   
10114  BANKEX  55800PE 2024-05-30 15:23:00  624.00  630.00  624.00  626.20   
10138  BANKEX  55800CE 2024-05-30 15:24:00  596.10  596.10  590.05  593.15   
10139  BANKEX  55800PE 2024-05-30 15:24:00  620.35  623.50  616.45  623.50   
10174  BANKEX  55800CE 2024-05-30 15:25:00  605.75  616.30  594.60  603.30   
10175  BANKEX  55800PE 2024-05-30 15:25:00  620.00  620.00  606.05  610.95   

       volume  openinterest 

102

ha
start_time found
he
heel
        index    scrip           date_time    open    high     low   close  \
710    BANKEX  57500PE 2024-06-03 09:20:00  290.00  431.60  290.00  425.95   
711    BANKEX  57500CE 2024-06-03 09:20:00  568.55  576.50  464.45  466.10   
846    BANKEX  57500PE 2024-06-03 09:21:00  425.35  491.45  396.90  411.60   
847    BANKEX  57500CE 2024-06-03 09:21:00  473.55  499.25  443.10  461.15   
977    BANKEX  57500CE 2024-06-03 09:22:00  455.70  455.70  321.55  345.60   
...       ...      ...                 ...     ...     ...     ...     ...   
48939  BANKEX  57500CE 2024-06-03 15:23:00  755.85  762.15  755.85  762.15   
49029  BANKEX  57500PE 2024-06-03 15:24:00    0.10    0.15    0.10    0.10   
49063  BANKEX  57500CE 2024-06-03 15:24:00  765.65  776.60  763.90  776.45   
49138  BANKEX  57500PE 2024-06-03 15:25:00    0.15    0.15    0.10    0.10   
49182  BANKEX  57500CE 2024-06-03 15:25:00  776.10  785.90  772.00  784.60   

       volume  openinterest ex

       index    scrip           date_time    open    high     low   close  \
399   BANKEX  53100PE 2024-06-05 10:37:00  692.65  703.80  682.90  682.90   
428   BANKEX  53100PE 2024-06-05 10:41:00  660.45  660.45  660.45  660.45   
515   BANKEX  53100PE 2024-06-05 10:51:00  517.30  517.30  517.30  517.30   
532   BANKEX  53100PE 2024-06-05 10:52:00  514.15  514.15  514.15  514.15   
551   BANKEX  53100PE 2024-06-05 10:53:00  497.30  497.30  486.10  486.10   
631   BANKEX  53100PE 2024-06-05 10:59:00  340.00  368.30  340.00  368.30   
686   BANKEX  53100PE 2024-06-05 11:03:00  310.20  310.20  310.00  310.00   
743   BANKEX  53100PE 2024-06-05 11:08:00  275.95  275.95  272.40  272.40   
761   BANKEX  53100PE 2024-06-05 11:09:00  276.60  276.60  276.60  276.60   
797   BANKEX  53100PE 2024-06-05 11:11:00  203.05  203.05  203.05  203.05   
816   BANKEX  53100PE 2024-06-05 11:12:00  221.95  221.95  221.95  221.95   
982   BANKEX  53100PE 2024-06-05 11:21:00  237.90  237.90  237.90  237.90   

2025-03-12 11:00:00
       index    scrip           date_time    open    high     low   close  \
687   BANKEX  53200PE 2024-06-05 11:03:00  351.35  351.35  351.35  351.35   
701   BANKEX  53200PE 2024-06-05 11:04:00  353.40  353.40  326.10  326.10   
744   BANKEX  53200PE 2024-06-05 11:08:00  307.10  307.10  307.10  307.10   
798   BANKEX  53200PE 2024-06-05 11:11:00  224.50  238.00  224.50  228.00   
894   BANKEX  53200PE 2024-06-05 11:16:00  236.40  236.40  236.40  236.40   
1042  BANKEX  53200PE 2024-06-05 11:26:00  220.50  220.50  189.60  189.60   
1073  BANKEX  53200PE 2024-06-05 11:28:00  216.95  216.95  216.95  216.95   
1099  BANKEX  53200PE 2024-06-05 11:29:00  215.05  215.05  215.05  215.05   
1277  BANKEX  53200PE 2024-06-05 11:38:00  221.85  221.85  221.85  221.85   
1554  BANKEX  53200PE 2024-06-05 11:51:00  277.30  277.70  277.30  277.70   
1599  BANKEX  53200PE 2024-06-05 11:53:00  295.45  302.05  295.45  302.05   
1648  BANKEX  53200PE 2024-06-05 11:55:00  298.95  308.6

2025-03-12 11:07:00
       index    scrip           date_time    open    high     low   close  \
687   BANKEX  53200PE 2024-06-05 11:03:00  351.35  351.35  351.35  351.35   
701   BANKEX  53200PE 2024-06-05 11:04:00  353.40  353.40  326.10  326.10   
744   BANKEX  53200PE 2024-06-05 11:08:00  307.10  307.10  307.10  307.10   
798   BANKEX  53200PE 2024-06-05 11:11:00  224.50  238.00  224.50  228.00   
894   BANKEX  53200PE 2024-06-05 11:16:00  236.40  236.40  236.40  236.40   
1042  BANKEX  53200PE 2024-06-05 11:26:00  220.50  220.50  189.60  189.60   
1073  BANKEX  53200PE 2024-06-05 11:28:00  216.95  216.95  216.95  216.95   
1099  BANKEX  53200PE 2024-06-05 11:29:00  215.05  215.05  215.05  215.05   
1277  BANKEX  53200PE 2024-06-05 11:38:00  221.85  221.85  221.85  221.85   
1554  BANKEX  53200PE 2024-06-05 11:51:00  277.30  277.70  277.30  277.70   
1599  BANKEX  53200PE 2024-06-05 11:53:00  295.45  302.05  295.45  302.05   
1648  BANKEX  53200PE 2024-06-05 11:55:00  298.95  308.6

...

2025-03-12 17:20:00
       index    scrip           date_time    open    high     low   close  \
687   BANKEX  53200PE 2024-06-05 11:03:00  351.35  351.35  351.35  351.35   
701   BANKEX  53200PE 2024-06-05 11:04:00  353.40  353.40  326.10  326.10   
744   BANKEX  53200PE 2024-06-05 11:08:00  307.10  307.10  307.10  307.10   
798   BANKEX  53200PE 2024-06-05 11:11:00  224.50  238.00  224.50  228.00   
894   BANKEX  53200PE 2024-06-05 11:16:00  236.40  236.40  236.40  236.40   
1042  BANKEX  53200PE 2024-06-05 11:26:00  220.50  220.50  189.60  189.60   
1073  BANKEX  53200PE 2024-06-05 11:28:00  216.95  216.95  216.95  216.95   
1099  BANKEX  53200PE 2024-06-05 11:29:00  215.05  215.05  215.05  215.05   
1277  BANKEX  53200PE 2024-06-05 11:38:00  221.85  221.85  221.85  221.85   
1554  BANKEX  53200PE 2024-06-05 11:51:00  277.30  277.70  277.30  277.70   
1599  BANKEX  53200PE 2024-06-05 11:53:00  295.45  302.05  295.45  302.05   
1648  BANKEX  53200PE 2024-06-05 11:55:00  298.95  308.6

       index    scrip           date_time    open    high     low   close  \
687   BANKEX  53200PE 2024-06-05 11:03:00  351.35  351.35  351.35  351.35   
701   BANKEX  53200PE 2024-06-05 11:04:00  353.40  353.40  326.10  326.10   
744   BANKEX  53200PE 2024-06-05 11:08:00  307.10  307.10  307.10  307.10   
798   BANKEX  53200PE 2024-06-05 11:11:00  224.50  238.00  224.50  228.00   
894   BANKEX  53200PE 2024-06-05 11:16:00  236.40  236.40  236.40  236.40   
1042  BANKEX  53200PE 2024-06-05 11:26:00  220.50  220.50  189.60  189.60   
1073  BANKEX  53200PE 2024-06-05 11:28:00  216.95  216.95  216.95  216.95   
1099  BANKEX  53200PE 2024-06-05 11:29:00  215.05  215.05  215.05  215.05   
1277  BANKEX  53200PE 2024-06-05 11:38:00  221.85  221.85  221.85  221.85   
1554  BANKEX  53200PE 2024-06-05 11:51:00  277.30  277.70  277.30  277.70   
1599  BANKEX  53200PE 2024-06-05 11:53:00  295.45  302.05  295.45  302.05   
1648  BANKEX  53200PE 2024-06-05 11:55:00  298.95  308.65  298.95  308.65   

       index    scrip           date_time    open    high     low   close  \
687   BANKEX  53200PE 2024-06-05 11:03:00  351.35  351.35  351.35  351.35   
701   BANKEX  53200PE 2024-06-05 11:04:00  353.40  353.40  326.10  326.10   
744   BANKEX  53200PE 2024-06-05 11:08:00  307.10  307.10  307.10  307.10   
798   BANKEX  53200PE 2024-06-05 11:11:00  224.50  238.00  224.50  228.00   
894   BANKEX  53200PE 2024-06-05 11:16:00  236.40  236.40  236.40  236.40   
1042  BANKEX  53200PE 2024-06-05 11:26:00  220.50  220.50  189.60  189.60   
1073  BANKEX  53200PE 2024-06-05 11:28:00  216.95  216.95  216.95  216.95   
1099  BANKEX  53200PE 2024-06-05 11:29:00  215.05  215.05  215.05  215.05   
1277  BANKEX  53200PE 2024-06-05 11:38:00  221.85  221.85  221.85  221.85   
1554  BANKEX  53200PE 2024-06-05 11:51:00  277.30  277.70  277.30  277.70   
1599  BANKEX  53200PE 2024-06-05 11:53:00  295.45  302.05  295.45  302.05   
1648  BANKEX  53200PE 2024-06-05 11:55:00  298.95  308.65  298.95  308.65   

       index    scrip           date_time    open    high     low   close  \
437   BANKEX  53300PE 2024-06-05 10:43:00  691.75  691.75  691.75  691.75   
467   BANKEX  53300PE 2024-06-05 10:47:00  658.75  658.75  658.75  658.75   
481   BANKEX  53300PE 2024-06-05 10:48:00  658.75  658.75  658.75  658.75   
518   BANKEX  53300PE 2024-06-05 10:51:00  592.85  592.85  592.85  592.85   
535   BANKEX  53300PE 2024-06-05 10:52:00  592.85  592.85  592.85  592.85   
...      ...      ...                 ...     ...     ...     ...     ...   
5903  BANKEX  53300PE 2024-06-05 15:09:00   76.75   76.75   76.75   76.75   
6035  BANKEX  53300PE 2024-06-05 15:15:00   74.65   74.65   74.65   74.65   
6204  BANKEX  53300PE 2024-06-05 15:20:00   80.45   80.45   80.30   80.30   
6254  BANKEX  53300PE 2024-06-05 15:21:00   85.45   85.45   81.00   81.00   
6399  BANKEX  53300PE 2024-06-05 15:25:00  103.20  103.20   98.10   99.00   

      volume  openinterest expiry_date  dte  
437       15            60  2


KeyboardInterrupt



In [140]:
strike

53500

In [141]:
df1

index    scrip           date_time     open     high      low    close  \
230   BANKEX  53500PE 2024-06-05 10:14:00   697.95   697.95   697.95   697.95   
366   BANKEX  53500CE 2024-06-05 10:34:00   690.50   690.50   690.50   690.50   
376   BANKEX  53500CE 2024-06-05 10:35:00   677.65   725.05   677.65   725.05   
386   BANKEX  53500PE 2024-06-05 10:36:00   989.10  1038.55   989.10  1038.55   
398   BANKEX  53500CE 2024-06-05 10:37:00   652.50   652.50   652.50   652.50   
...      ...      ...                 ...      ...      ...      ...      ...   
6445  BANKEX  53500CE 2024-06-05 15:25:00  2260.15  2260.15  2217.10  2217.10   
6448  BANKEX  53500PE 2024-06-05 15:26:00   116.85   121.10   116.85   119.90   
6492  BANKEX  53500PE 2024-06-05 15:27:00   123.50   123.50   122.20   122.20   
6542  BANKEX  53500PE 2024-06-05 15:28:00   105.65   105.65   105.65   105.65   
6574  BANKEX  53500PE 2024-06-05 15:29:00   109.20   109.20    70.05    70.05   

      volume  openinterest expiry_date  dte  
230       15            30  2024-06-10    5  
366       30             0  2024-06-10    5  
376       45             0  2024-06-10    5  
386       90            45  2024-06-10    5  
398       75            75  2024-06-10    5  
...      ...           ...         ...  ...  
6445     195          6915  2024-06-10    5  
6448     150          2310  2024-06-10    5  
6492      45          2190  2024-06-10    5  
6542      60          2190  2024-06-10    5  
6574     135          2190  2024-06-10    5  

[251 rows x 11 columns]

In [142]:
df2

index    scrip           date_time   open   high    low  close  volume  \
398  BANKEX  53500CE 2024-06-05 10:37:00  652.5  652.5  652.5  652.5      75   

     openinterest expiry_date  dte  
398            75  2024-06-10    5

In [143]:
df3

index    scrip           date_time     open    high     low   close  \
400  BANKEX  53500PE 2024-06-05 10:37:00  1038.55  1090.5  997.65  997.65   

     volume  openinterest expiry_date  dte  
400     195            45  2024-06-10    5

In [144]:
dataframe1[(dataframe1['scrip'] == f'{strike}CE') |  (dataframe1['scrip'] == f'{strike}PE')]

index    scrip           date_time     open     high      low    close  \
230   BANKEX  53500PE 2024-06-05 10:14:00   697.95   697.95   697.95   697.95   
366   BANKEX  53500CE 2024-06-05 10:34:00   690.50   690.50   690.50   690.50   
376   BANKEX  53500CE 2024-06-05 10:35:00   677.65   725.05   677.65   725.05   
386   BANKEX  53500PE 2024-06-05 10:36:00   989.10  1038.55   989.10  1038.55   
398   BANKEX  53500CE 2024-06-05 10:37:00   652.50   652.50   652.50   652.50   
...      ...      ...                 ...      ...      ...      ...      ...   
6445  BANKEX  53500CE 2024-06-05 15:25:00  2260.15  2260.15  2217.10  2217.10   
6448  BANKEX  53500PE 2024-06-05 15:26:00   116.85   121.10   116.85   119.90   
6492  BANKEX  53500PE 2024-06-05 15:27:00   123.50   123.50   122.20   122.20   
6542  BANKEX  53500PE 2024-06-05 15:28:00   105.65   105.65   105.65   105.65   
6574  BANKEX  53500PE 2024-06-05 15:29:00   109.20   109.20    70.05    70.05   

      volume  openinterest expiry_date  dte  
230       15            30  2024-06-10    5  
366       30             0  2024-06-10    5  
376       45             0  2024-06-10    5  
386       90            45  2024-06-10    5  
398       75            75  2024-06-10    5  
...      ...           ...         ...  ...  
6445     195          6915  2024-06-10    5  
6448     150          2310  2024-06-10    5  
6492      45          2190  2024-06-10    5  
6542      60          2190  2024-06-10    5  
6574     135          2190  2024-06-10    5  

[251 rows x 11 columns]

In [128]:
dataframe2

index    scrip           date_time    open    high     low   close  \
711    BANKEX  57500CE 2024-06-03 09:20:00  568.55  576.50  464.45  466.10   
847    BANKEX  57500CE 2024-06-03 09:21:00  473.55  499.25  443.10  461.15   
977    BANKEX  57500CE 2024-06-03 09:22:00  455.70  455.70  321.55  345.60   
1116   BANKEX  57500CE 2024-06-03 09:23:00  337.60  380.70  329.75  353.75   
1258   BANKEX  57500CE 2024-06-03 09:24:00  352.30  432.70  341.10  369.00   
...       ...      ...                 ...     ...     ...     ...     ...   
48689  BANKEX  57500CE 2024-06-03 15:21:00  758.60  762.10  752.40  753.90   
48814  BANKEX  57500CE 2024-06-03 15:22:00  755.70  761.05  752.25  761.05   
48939  BANKEX  57500CE 2024-06-03 15:23:00  755.85  762.15  755.85  762.15   
49063  BANKEX  57500CE 2024-06-03 15:24:00  765.65  776.60  763.90  776.45   
49182  BANKEX  57500CE 2024-06-03 15:25:00  776.10  785.90  772.00  784.60   

       volume  openinterest expiry_date  dte  
711     68445         96150  2024-06-03    0  
847     63840        105615  2024-06-03    0  
977    113025        105615  2024-06-03    0  
1116   113535        105615  2024-06-03    0  
1258   116700        150615  2024-06-03    0  
...       ...           ...         ...  ...  
48689    1875        178125  2024-06-03    0  
48814     615        178125  2024-06-03    0  
48939     945        178125  2024-06-03    0  
49063    1470        177510  2024-06-03    0  
49182    9690        177510  2024-06-03    0  

[366 rows x 11 columns]

In [129]:
dataframe3

index    scrip           date_time    open    high     low   close  \
710    BANKEX  57500PE 2024-06-03 09:20:00  290.00  431.60  290.00  425.95   
846    BANKEX  57500PE 2024-06-03 09:21:00  425.35  491.45  396.90  411.60   
986    BANKEX  57500PE 2024-06-03 09:22:00  410.00  612.65  401.75  583.25   
1123   BANKEX  57500PE 2024-06-03 09:23:00  597.15  603.30  505.95  538.30   
1261   BANKEX  57500PE 2024-06-03 09:24:00  536.90  543.25  392.95  441.00   
...       ...      ...                 ...     ...     ...     ...     ...   
48630  BANKEX  57500PE 2024-06-03 15:21:00    0.15    0.20    0.10    0.10   
48787  BANKEX  57500PE 2024-06-03 15:22:00    0.15    0.15    0.10    0.15   
48910  BANKEX  57500PE 2024-06-03 15:23:00    0.10    0.15    0.10    0.15   
49029  BANKEX  57500PE 2024-06-03 15:24:00    0.10    0.15    0.10    0.10   
49138  BANKEX  57500PE 2024-06-03 15:25:00    0.15    0.15    0.10    0.10   

       volume  openinterest expiry_date  dte  
710     93345         42270  2024-06-03    0  
846    112185         84030  2024-06-03    0  
986    102195         84030  2024-06-03    0  
1123    79830         84030  2024-06-03    0  
1261    87285        105885  2024-06-03    0  
...       ...           ...         ...  ...  
48630   86715        735330  2024-06-03    0  
48787   40710        735330  2024-06-03    0  
48910   16125        735330  2024-06-03    0  
49029   45915        694020  2024-06-03    0  
49138   71325        694020  2024-06-03    0  

[366 rows x 11 columns]

In [ ]:
if (df2.date_time.dt.strftime("%H:%M:%S") == start_time).any() and \
    (df3.date_time.dt.strftime("%H:%M:%S") == start_time).any():
    time_flag = True